In [1]:
# to add the spiking model codebase to the path
import sys
sys.path.append('..')

%matplotlib
import matplotlib.pyplot as plt
import matplotlib.colors as colors
from matplotlib.animation import FuncAnimation, writers
# plt.style.use('seaborn-pastel')
plt.rcParams['animation.ffmpeg_path'] ='C:\\ffmpeg\\bin\\ffmpeg.exe'

from brian2 import pA, Hz, second, ms
import numpy as np

from results import Results
from plot import (MidpointNormalize, weight_matrix, remove_axes_less, prune_figure, prune_figure_less, prune_figure_more,
                  plot_spike_raster, plot_firing_rate, plot_voltage_detail)
from generate import weight_matrix_from_flat_inds_weights

Using matplotlib backend: Qt5Agg


INFO       Cache size for target "cython": 10688 MB.
You can call "clear_cache('cython')" to delete all files from the cache or manually delete files in the "C:\Users\mikejseay\.cython\brian_extensions" directory. [brian2]


In [2]:
targetPath = 'C:/Users/mikejseay/Documents/BrianResults/'
targetFile = 'classicJercog_1000_0p5_balance_randomUniformSaray_movieTest_2021-05-14-08-22_results'

R = Results()
R.init_from_file(targetFile, targetPath)

downSampleFactorForE = 0.025
downSampleFactorForI = 0.1

if R.p['useRule'] == 'cross-homeo':
    R.p['alpha2'] = -1e-12
    R.p['tauPlasticityTrials'] = None
if 'wEEScale' not in R.p:
    R.p['wEEScale'] = None
    R.p['wIEScale'] = None
    R.p['wEIScale'] = None
    R.p['wIIScale'] = None

importantInfoString = 'Name: {}\nEE: {}, IE: {}, EI: {}, II: {}\n tauFR={}, a1={:.4f} pA, a2={:.4f} pA, tauP={}'.format(R.rID,
    R.p['wEEScale'],R.p['wIEScale'],R.p['wEIScale'],R.p['wIIScale'],
    R.p['tauUpFRTrials'], R.p['alpha1'] / pA, R.p['alpha2'] / pA, R.p['tauPlasticityTrials'])

wEEInit = weight_matrix_from_flat_inds_weights(R.p['nExc'], R.p['nExc'], R.preEE, R.posEE, R.wEE_init)
wIEInit = weight_matrix_from_flat_inds_weights(R.p['nExc'], R.p['nInh'], R.preIE, R.posIE, R.wIE_init)
wEIInit = weight_matrix_from_flat_inds_weights(R.p['nInh'], R.p['nExc'], R.preEI, R.posEI, R.wEI_init)
wIIInit = weight_matrix_from_flat_inds_weights(R.p['nInh'], R.p['nInh'], R.preII, R.posII, R.wII_init)

wEEFinal = weight_matrix_from_flat_inds_weights(R.p['nExc'], R.p['nExc'], R.preEE, R.posEE, R.wEE_final)
wIEFinal = weight_matrix_from_flat_inds_weights(R.p['nExc'], R.p['nInh'], R.preIE, R.posIE, R.wIE_final)
wEIFinal = weight_matrix_from_flat_inds_weights(R.p['nInh'], R.p['nExc'], R.preEI, R.posEI, R.wEI_final)
wIIFinal = weight_matrix_from_flat_inds_weights(R.p['nInh'], R.p['nInh'], R.preII, R.posII, R.wII_final)

wFullInit = np.block([[wEEInit, wIEInit], [-wEIInit, -wIIInit]])
wFullFinal = np.block([[wEEFinal, wIEFinal], [-wEIFinal, -wIIFinal]])

# get summed presynaptic input to each unit

wEEInitP = np.nansum(wEEInit, 0)
wIEInitP = np.nansum(wIEInit, 0)
wEIInitP = np.nansum(wEIInit, 0)
wIIInitP = np.nansum(wIIInit, 0)

wEEFinalP = np.nansum(wEEFinal, 0)
wIEFinalP = np.nansum(wIEFinal, 0)
wEIFinalP = np.nansum(wEIFinal, 0)
wIIFinalP = np.nansum(wIIFinal, 0)

downSampleNForE = int(downSampleFactorForE * R.p['nExc'])
downSampleNForI = int(downSampleFactorForI * R.p['nInh'])

downSampleE = np.random.choice(R.p['nExc'], size=downSampleNForE, replace=False)
downSampleI = np.random.choice(R.p['nInh'], size=downSampleNForI, replace=False)

In [7]:
plt.close('all')

- idea is to draw a movie of the change in average FR and weights across *trials* between trial n1 and n2
- then draw the movie of a single trial (n2)
- then draw the trials from n2 to n3
- then draw the movie of a single trial (n3)

In [9]:
clipVeryHighFRs = False
yMax = 40
commonXLims = (0, R.trialUpFRExcUnits.shape[0])
commonTrialRange = np.arange(0, R.trialUpFRExcUnits.shape[0])

if clipVeryHighFRs:
    tmptrialUpFRExcUnits = R.trialUpFRExcUnits.copy()
    tmptrialUpFRInhUnits = R.trialUpFRInhUnits.copy()
    tmptrialUpFRExcUnits[R.trialUpFRExcUnits > R.p['maxAllowedFRExc']] = np.nan
    tmptrialUpFRInhUnits[R.trialUpFRInhUnits > R.p['maxAllowedFRInh']] = np.nan
else:
    tmptrialUpFRExcUnits = R.trialUpFRExcUnits.copy()
    tmptrialUpFRInhUnits = R.trialUpFRInhUnits.copy()
    
# for useTrialInd in range(1, len(R.p['saveTrials'])):
useTrialInd = 9
    
useTrialRange = np.arange(0, R.p['saveTrials'][useTrialInd])

trialwEE = R.trialwEE[useTrialRange]
trialwIE = R.trialwIE[useTrialRange]
trialwEI = R.trialwEI[useTrialRange]
trialwII = R.trialwII[useTrialRange]

#     FRExcUnits = tmptrialUpFRExcUnits[useTrialRange, downSampleE]
#     FRInhUnits = tmptrialUpFRInhUnits[useTrialRange, downSampleI]
FRExcUnits = tmptrialUpFRExcUnits[useTrialRange, :][:, downSampleE]
FRInhUnits = tmptrialUpFRInhUnits[useTrialRange, :][:, downSampleI]

trialUpFRExc = R.trialUpFRExc[useTrialRange]
trialUpFRInh = R.trialUpFRInh[useTrialRange]

fig2, ax2 = plt.subplots(3, 1, sharex=True, figsize=(7, 9))

wAx, frEAx, frIAx = ax2

wAx.set(xlim=commonXLims, ylim=(0, 20), ylabel='Weight (pA)')
frEAx.set(xlim=commonXLims, ylim=(0, 30), ylabel='Firing Rate (Hz)')
frIAx.set(xlim=commonXLims, ylim=(0, 30), ylabel='Firing Rate (Hz)', xlabel='Trial #')

wHandleEE, = wAx.plot([], [], color='cyan', label='jEE')
wHandleIE, = wAx.plot([], [], color='purple', label='jIE')
wHandleEI, = wAx.plot([], [], color='cyan', label='jEI', ls='--')
wHandleII, = wAx.plot([], [], color='purple', label='jII', ls='--')

frHandleIndivE, = frEAx.plot([], [], color='g', alpha=0.2)
frHandleMeanE, = frEAx.plot([], [], color='darkgreen', lw=3)
frHandleIndivI, = frIAx.plot([], [], color='r', alpha=0.2)
frHandleMeanI, = frIAx.plot([], [], color='darkred', lw=3)

def init():
    wHandleEE.set_data([], [])
    wHandleIE.set_data([], [])
    wHandleEI.set_data([], [])
    wHandleII.set_data([], [])
    
    frHandleIndivE.set_data([0,], np.zeros((downSampleE.size,)))
    frHandleIndivI.set_data([0,], np.zeros((downSampleE.size,)))
    
    frHandleMeanE.set_data([], [])
    frHandleMeanI.set_data([], [])

    print('initalized animation')

    return wHandleEE, wHandleIE, wHandleEI, wHandleII, frHandleIndivE, frHandleMeanE, frHandleIndivI, frHandleMeanI,

def animate(i):
    wHandleEE.set_data(useTrialRange[:i], trialwEE[:i])
    wHandleIE.set_data(useTrialRange[:i], trialwIE[:i])
    wHandleEI.set_data(useTrialRange[:i], trialwEI[:i])
    wHandleII.set_data(useTrialRange[:i], trialwII[:i])

    frHandleIndivE.set_data(useTrialRange[:i], FRExcUnits[:i, :])
    frHandleIndivI.set_data(useTrialRange[:i], FRInhUnits[:i, :])

    frHandleMeanE.set_data(useTrialRange[:i], trialUpFRExc[:i])
    frHandleMeanI.set_data(useTrialRange[:i], trialUpFRInh[:i])

    print('animated frame', i)

    return wHandleEE, wHandleIE, wHandleEI, wHandleII, frHandleIndivE, frHandleMeanE, frHandleIndivI, frHandleMeanI,

useFPS = 30
totalFrames = useTrialRange.size
framesToSave = np.arange(0, useTrialRange.size)

anim = FuncAnimation(fig2, animate, init_func=init,
                     frames=framesToSave, blit=True, repeat=True)
# anim.save('trial' + str(useTrialInd) + '.gif')

#     Writer = writers['ffmpeg']
#     writer = Writer(fps=useFPS)
#     anim.save('weightFRtrial' + str(R.p['saveTrials'][useTrialInd] + 1) + '.mp4', writer=writer)

initalized animation
initalized animation
animated frame 0
animated frame 1
animated frame 2
animated frame 3
animated frame 4
animated frame 5
animated frame 6
animated frame 7
animated frame 8
animated frame 9
animated frame 10
animated frame 11
animated frame 12
animated frame 13
animated frame 14
animated frame 15
animated frame 16
animated frame 17
animated frame 18
animated frame 19
animated frame 20
animated frame 21
animated frame 22
animated frame 23
animated frame 24
animated frame 25
animated frame 26
animated frame 27
animated frame 28
animated frame 29
animated frame 30
animated frame 31
animated frame 32
animated frame 33
animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
animated frame 42
animated frame 43
animated frame 44
animated frame 45
animated frame 46
animated frame 47
animated frame 48
animated frame 49
animated frame 50
animated frame 51
animated frame 52
animated frame

animated frame 16
animated frame 17
animated frame 18
animated frame 19
animated frame 20
animated frame 21
animated frame 22
animated frame 23
animated frame 24
animated frame 25
animated frame 26
animated frame 27
animated frame 28
animated frame 29
animated frame 30
animated frame 31
animated frame 32
animated frame 33
animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
animated frame 42
animated frame 43
animated frame 44
animated frame 45
animated frame 46
animated frame 47
animated frame 48
animated frame 49
animated frame 50
animated frame 51
animated frame 52
animated frame 53
animated frame 54
animated frame 55
animated frame 56
animated frame 57
animated frame 58
animated frame 59
animated frame 60
animated frame 61
animated frame 62
animated frame 63
animated frame 64
animated frame 65
animated frame 66
animated frame 67
animated frame 68
animated frame 69
animated frame 70
animated f

animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
animated frame 42
animated frame 43
animated frame 44
animated frame 45
animated frame 46
animated frame 47
animated frame 48
animated frame 49
animated frame 50
animated frame 51
animated frame 52
animated frame 53
animated frame 54
animated frame 55
animated frame 56
animated frame 57
animated frame 58
animated frame 59
animated frame 60
animated frame 61
animated frame 62
animated frame 63
animated frame 64
animated frame 65
animated frame 66
animated frame 67
animated frame 68
animated frame 69
animated frame 70
animated frame 71
animated frame 72
animated frame 73
animated frame 74
animated frame 75
animated frame 76
animated frame 77
animated frame 78
animated frame 79
animated frame 80
animated frame 81
animated frame 82
animated frame 83
animated frame 84
animated frame 85
animated frame 86
animated frame 87
animated frame 88
animated f

animated frame 52
animated frame 53
animated frame 54
animated frame 55
animated frame 56
animated frame 57
animated frame 58
animated frame 59
animated frame 60
animated frame 61
animated frame 62
animated frame 63
animated frame 64
animated frame 65
animated frame 66
animated frame 67
animated frame 68
animated frame 69
animated frame 70
animated frame 71
animated frame 72
animated frame 73
animated frame 74
animated frame 75
animated frame 76
animated frame 77
animated frame 78
animated frame 79
animated frame 80
animated frame 81
animated frame 82
animated frame 83
animated frame 84
animated frame 85
animated frame 86
animated frame 87
animated frame 88
animated frame 89
animated frame 90
animated frame 91
animated frame 92
animated frame 93
animated frame 94
animated frame 95
animated frame 96
animated frame 97
animated frame 98
animated frame 99
animated frame 100
animated frame 101
animated frame 102
animated frame 103
animated frame 104
animated frame 105
animated frame 106
ani

animated frame 70
animated frame 71
animated frame 72
animated frame 73
animated frame 74
animated frame 75
animated frame 76
animated frame 77
animated frame 78
animated frame 79
animated frame 80
animated frame 81
animated frame 82
animated frame 83
animated frame 84
animated frame 85
animated frame 86
animated frame 87
animated frame 88
animated frame 89
animated frame 90
animated frame 91
animated frame 92
animated frame 93
animated frame 94
animated frame 95
animated frame 96
animated frame 97
animated frame 98
animated frame 99
animated frame 100
animated frame 101
animated frame 102
animated frame 103
animated frame 104
animated frame 105
animated frame 106
animated frame 107
animated frame 108
animated frame 109
animated frame 110
animated frame 111
animated frame 112
animated frame 113
animated frame 114
animated frame 115
animated frame 116
animated frame 117
animated frame 118
animated frame 119
animated frame 120
animated frame 121
animated frame 122
animated frame 123
anim

...

animated frame 97
animated frame 98
animated frame 99
animated frame 100
animated frame 101
animated frame 102
animated frame 103
animated frame 104
animated frame 105
animated frame 106
animated frame 107
animated frame 108
animated frame 109
animated frame 110
animated frame 111
animated frame 112
animated frame 113
animated frame 114
animated frame 115
animated frame 116
animated frame 117
animated frame 118
animated frame 119
animated frame 120
animated frame 121
animated frame 122
animated frame 123
animated frame 124
animated frame 125
animated frame 126
animated frame 127
animated frame 128
animated frame 129
animated frame 130
animated frame 131
animated frame 132
animated frame 133
animated frame 134
animated frame 135
animated frame 136
animated frame 137
animated frame 138
animated frame 139
animated frame 140
animated frame 141
animated frame 142
initalized animation
animated frame 0
animated frame 1
animated frame 2
animated frame 3
animated frame 4
animated frame 5
animat

animated frame 114
animated frame 115
animated frame 116
animated frame 117
animated frame 118
animated frame 119
animated frame 120
animated frame 121
animated frame 122
animated frame 123
animated frame 124
animated frame 125
animated frame 126
animated frame 127
animated frame 128
animated frame 129
animated frame 130
animated frame 131
animated frame 132
animated frame 133
animated frame 134
animated frame 135
animated frame 136
animated frame 137
animated frame 138
animated frame 139
animated frame 140
animated frame 141
animated frame 142
initalized animation
animated frame 0
animated frame 1
animated frame 2
animated frame 3
animated frame 4
animated frame 5
animated frame 6
animated frame 7
animated frame 8
animated frame 9
animated frame 10
animated frame 11
animated frame 12
animated frame 13
animated frame 14
animated frame 15
animated frame 16
animated frame 17
animated frame 18
animated frame 19
animated frame 20
animated frame 21
animated frame 22
animated frame 23
animat

animated frame 131
animated frame 132
animated frame 133
animated frame 134
animated frame 135
animated frame 136
animated frame 137
animated frame 138
animated frame 139
animated frame 140
animated frame 141
animated frame 142
initalized animation
animated frame 0
animated frame 1
animated frame 2
animated frame 3
animated frame 4
animated frame 5
animated frame 6
animated frame 7
animated frame 8
animated frame 9
animated frame 10
animated frame 11
animated frame 12
animated frame 13
animated frame 14
animated frame 15
animated frame 16
animated frame 17
animated frame 18
animated frame 19
animated frame 20
animated frame 21
animated frame 22
animated frame 23
animated frame 24
animated frame 25
animated frame 26
animated frame 27
animated frame 28
animated frame 29
animated frame 30
animated frame 31
animated frame 32
animated frame 33
animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
anima

animated frame 3
animated frame 4
animated frame 5
animated frame 6
animated frame 7
animated frame 8
animated frame 9
animated frame 10
animated frame 11
animated frame 12
animated frame 13
animated frame 14
animated frame 15
animated frame 16
animated frame 17
animated frame 18
animated frame 19
animated frame 20
animated frame 21
animated frame 22
animated frame 23
animated frame 24
animated frame 25
animated frame 26
animated frame 27
animated frame 28
animated frame 29
animated frame 30
animated frame 31
animated frame 32
animated frame 33
animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
animated frame 42
animated frame 43
animated frame 44
animated frame 45
animated frame 46
animated frame 47
animated frame 48
animated frame 49
animated frame 50
animated frame 51
animated frame 52
animated frame 53
animated frame 54
animated frame 55
animated frame 56
animated frame 57
animated frame 58

animated frame 20
animated frame 21
animated frame 22
animated frame 23
animated frame 24
animated frame 25
animated frame 26
animated frame 27
animated frame 28
animated frame 29
animated frame 30
animated frame 31
animated frame 32
animated frame 33
animated frame 34
animated frame 35
animated frame 36
animated frame 37
animated frame 38
animated frame 39
animated frame 40
animated frame 41
animated frame 42
animated frame 43
animated frame 44
animated frame 45
animated frame 46
animated frame 47
animated frame 48
animated frame 49
animated frame 50
animated frame 51
animated frame 52
animated frame 53
animated frame 54
animated frame 55
animated frame 56
animated frame 57
animated frame 58
animated frame 59
animated frame 60
animated frame 61
animated frame 62
animated frame 63
animated frame 64
animated frame 65
animated frame 66
animated frame 67
animated frame 68
animated frame 69
animated frame 70
animated frame 71
animated frame 72
animated frame 73
animated frame 74
animated f

In [14]:
tmptrialUpFRExcUnits.shape

(987, 800)

In [15]:
useTrialRange

array([0, 1])

In [16]:
downSampleE

array([220, 219, 142,  16, 453, 396,  52,  62, 188, 595, 292, 386, 667,
         0, 392, 225, 644, 280, 327, 428, 560, 772,  64, 110, 387, 564,
        38, 600, 451,  78,  12, 746, 422, 388, 629, 645, 515,  71, 174,
       353, 441, 320, 368, 470, 550, 302, 635, 641, 134,  79, 405, 125,
       287,  32, 799, 771, 481, 178, 482, 457,  50, 270, 671, 584,  88,
       338, 345, 199, 732, 409, 184, 739, 207, 349,   9, 401, 189,  20,
       775, 631, 617, 144, 446, 251,  82, 664,  48, 289,  57, 179, 701,
       282,  87,  27, 692, 748, 649, 484, 370, 366])

In [17]:
test = tmptrialUpFRExcUnits[useTrialRange, :][:, downSampleE]

In [18]:
test.shape

(2, 100)

In [ ]:
ax[0].plot(R.trialwEE, label='wEE', color='cyan')
ax[0].plot(R.trialwIE, label='wIE', color='purple')
ax[0].plot(R.trialwEI, label='wEI', color='cyan', ls='--')
ax[0].plot(R.trialwII, label='wII', color='purple', ls='--')
ax[0].legend()
ax[0].set_xlabel('Trial #')
ax[0].set_ylabel('Weight (pA)')

ax[1].plot(tmptrialUpFRExcUnits[:, downSampleE], color='g', alpha=0.2)
ax[2].plot(tmptrialUpFRInhUnits[:, downSampleI], color='r', alpha=0.2)
ax[1].plot(R.trialUpFRExc, color='darkgreen', lw=3)
ax[2].plot(R.trialUpFRInh, color='darkred', lw=3)
ax[1].set(ylabel='Firing Rate (Hz)', ylim=(0, 30))
ax[2].set(ylabel='Firing Rate (Hz)', ylim=(0, 30))

In [9]:
frameMult = int(R.p['downSampleVoltageTo'] / R.p['dt'])
useUnitInd = 0
decreaseVoltageBy = 70
FRDT = 0.01  # seconds
voltageYLims = (-90, 10)
targetDisplayedExcUnits = 100
targetDisplayedInhUnits = 100

commonXLims = (0, R.p['duration'] / second)
voltageT = R.selectTrialT[1:]

for useTrialInd in range(len(R.p['saveTrials'])):

    voltageE = R.selectTrialVExc[useTrialInd, :] - decreaseVoltageBy
    vSpikeTimesE = R.selectTrialSpikeExcT[useTrialInd][R.selectTrialSpikeExcI[useTrialInd] == useUnitInd]
    vSpikeTimesIndE = (vSpikeTimesE / R.p['dt'] * second / frameMult).astype(int)
    voltageE[vSpikeTimesIndE] = 0

    voltageI = R.selectTrialVInh[useTrialInd, :] - decreaseVoltageBy
    vSpikeTimesI = R.selectTrialSpikeInhT[useTrialInd][R.selectTrialSpikeInhI[useTrialInd] == useUnitInd]
    vSpikeTimesIndI = (vSpikeTimesI / R.p['dt'] * second / frameMult).astype(int)
    voltageI[vSpikeTimesIndI] = 0

    FRT = np.arange(FRDT / 2, R.p['duration'] / second - FRDT / 2, FRDT)
    FRE = R.selectTrialFRExc[useTrialInd, :]
    FRI = R.selectTrialFRInh[useTrialInd, :]

    spikeMonExcT = R.selectTrialSpikeExcT[useTrialInd]
    spikeMonExcI = R.selectTrialSpikeExcI[useTrialInd]
    spikeMonInhT = R.selectTrialSpikeInhT[useTrialInd]
    spikeMonInhI = R.selectTrialSpikeInhI[useTrialInd]

    downSampleE = np.random.choice(R.p['nExc'], size=targetDisplayedExcUnits, replace=False)
    downSampleI = np.random.choice(R.p['nInh'], size=targetDisplayedInhUnits, replace=False)
    matchingEUnitsBool = np.isin(spikeMonExcI, downSampleE)
    matchingIUnitsBool = np.isin(spikeMonInhI, downSampleI)
    DownSampleERev = np.full((downSampleE.max() + 1,), np.nan)
    DownSampleERev[downSampleE] = np.arange(downSampleE.size)
    DownSampleIRev = np.full((downSampleI.max() + 1,), np.nan)
    DownSampleIRev[downSampleI] = np.arange(downSampleI.size)
    spikesExcT = spikeMonExcT[matchingEUnitsBool]
    spikesExcI = DownSampleERev[spikeMonExcI[matchingEUnitsBool].astype(int)]
    spikesInhT = spikeMonInhT[matchingIUnitsBool]
    spikesInhI = targetDisplayedExcUnits + DownSampleIRev[spikeMonInhI[matchingIUnitsBool].astype(int)]

    fig1, ax1 = plt.subplots(4, 1, num=1, figsize=(5, 9), gridspec_kw={'height_ratios': [2, 1, 1, 1]}, sharex=True)

    srAx, frAx, veAx, viAx = ax1

    srAx.set(xlim=commonXLims, ylim=(0, 200), ylabel='Unit Index')      # spike raster
    frAx.set(xlim=commonXLims, ylim=(0, 30), ylabel='Firing Rate (Hz)')       # FR
    veAx.set(xlim=commonXLims, ylim=voltageYLims, ylabel='mV')  # voltageE
    viAx.set(xlim=commonXLims, ylim=voltageYLims, ylabel='mV', xlabel='Time (s)')  # voltageI

    srHandleE, = srAx.plot([], [], c='g', ls='', marker='.', markersize=1)
    srHandleI, = srAx.plot([], [], c='r', ls='', marker='.', markersize=1)

    frHandleE, = frAx.plot([], [], c='g', label='Exc', alpha=0.5)
    frHandleI, = frAx.plot([], [], c='r', label='Inh', alpha=0.5)

    vHandleE, = veAx.plot([], [], c='g', lw=.3)
    vHandleI, = viAx.plot([], [], c='r', lw=.3)

    def init():
        srHandleE.set_data([], [])
        srHandleI.set_data([], [])
        frHandleE.set_data([], [])
        frHandleI.set_data([], [])
        vHandleE.set_data([], [])
        vHandleI.set_data([], [])

        print('initalized animation')

        return srHandleE, srHandleI, frHandleE, frHandleI, vHandleE, vHandleI, 

    def animate(i):
        vHandleE.set_data(voltageT[:i], voltageE[:i])
        vHandleI.set_data(voltageT[:i], voltageI[:i])

        fri = int(i / 10)
        frHandleE.set_data(FRT[:fri], FRE[:fri])
        frHandleI.set_data(FRT[:fri], FRI[:fri])

        currentTime = voltageT[i]
        sBoolE = spikesExcT <= currentTime
        sBoolI = spikesInhT <= currentTime
        srHandleE.set_data(spikesExcT[sBoolE], spikesExcI[sBoolE])
        srHandleI.set_data(spikesInhT[sBoolI], spikesInhI[sBoolI])

        print('animated frame', i)

        return srHandleE, srHandleI, frHandleE, frHandleI, vHandleE, vHandleI, 

    useFPS = 30
    totalFrames = int(np.round((voltageT[-1] * second) * useFPS * Hz))
    useInterval = int(np.round(voltageT.size / totalFrames))
    framesToSave = np.arange(0, voltageT.size, useInterval)

    anim = FuncAnimation(fig1, animate, init_func=init,
                         frames=framesToSave, blit=True, repeat=False)
    # anim.save('trial' + str(useTrialInd) + '.gif')

    Writer = writers['ffmpeg']
    writer = Writer(fps=useFPS)
    anim.save('trial' + str(R.p['saveTrials'][useTrialInd] + 1) + '.mp4', writer=writer)
    fig1.clear()

initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
ani

animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
an

TypeError: 'NoneType' object is not subscriptable

initalized animation
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485


In [9]:
frameMult = int(R.p['downSampleVoltageTo'] / R.p['dt'])
useUnitInd = 0
decreaseVoltageBy = 70
FRDT = 0.01  # seconds
voltageYLims = (-90, 10)
targetDisplayedExcUnits = 100
targetDisplayedInhUnits = 100

commonXLims = (0, R.p['duration'] / second)
voltageT = R.selectTrialT[1:]

voltageE = R.selectTrialVExc[useTrialInd, :] - decreaseVoltageBy
vSpikeTimesE = R.selectTrialSpikeExcT[useTrialInd][R.selectTrialSpikeExcI[useTrialInd] == useUnitInd]
vSpikeTimesIndE = (vSpikeTimesE / R.p['dt'] * second / frameMult).astype(int)
voltageE[vSpikeTimesIndE] = 0

voltageI = R.selectTrialVInh[useTrialInd, :] - decreaseVoltageBy
vSpikeTimesI = R.selectTrialSpikeInhT[useTrialInd][R.selectTrialSpikeInhI[useTrialInd] == useUnitInd]
vSpikeTimesIndI = (vSpikeTimesI / R.p['dt'] * second / frameMult).astype(int)
voltageI[vSpikeTimesIndI] = 0

FRT = np.arange(FRDT / 2, R.p['duration'] / second - FRDT / 2, FRDT)
FRE = R.selectTrialFRExc[useTrialInd, :]
FRI = R.selectTrialFRInh[useTrialInd, :]

spikeMonExcT = R.selectTrialSpikeExcT[useTrialInd]
spikeMonExcI = R.selectTrialSpikeExcI[useTrialInd]
spikeMonInhT = R.selectTrialSpikeInhT[useTrialInd]
spikeMonInhI = R.selectTrialSpikeInhI[useTrialInd]

downSampleE = np.random.choice(R.p['nExc'], size=targetDisplayedExcUnits, replace=False)
downSampleI = np.random.choice(R.p['nInh'], size=targetDisplayedInhUnits, replace=False)
matchingEUnitsBool = np.isin(spikeMonExcI, downSampleE)
matchingIUnitsBool = np.isin(spikeMonInhI, downSampleI)
DownSampleERev = np.full((downSampleE.max() + 1,), np.nan)
DownSampleERev[downSampleE] = np.arange(downSampleE.size)
DownSampleIRev = np.full((downSampleI.max() + 1,), np.nan)
DownSampleIRev[downSampleI] = np.arange(downSampleI.size)
spikesExcT = spikeMonExcT[matchingEUnitsBool]
spikesExcI = DownSampleERev[spikeMonExcI[matchingEUnitsBool].astype(int)]
spikesInhT = spikeMonInhT[matchingIUnitsBool]
spikesInhI = targetDisplayedExcUnits + DownSampleIRev[spikeMonInhI[matchingIUnitsBool].astype(int)]

fig1, ax1 = plt.subplots(4, 1, num=1, figsize=(5, 9), gridspec_kw={'height_ratios': [2, 1, 1, 1]}, sharex=True)

srAx, frAx, veAx, viAx = ax1

srAx.set(xlim=commonXLims, ylim=(0, 200), ylabel='Unit Index')      # spike raster
frAx.set(xlim=commonXLims, ylim=(0, 30), ylabel='Firing Rate (Hz)')       # FR
veAx.set(xlim=commonXLims, ylim=voltageYLims, ylabel='mV')  # voltageE
viAx.set(xlim=commonXLims, ylim=voltageYLims, ylabel='mV', xlabel='Time (s)')  # voltageI

srHandleE, = srAx.plot([], [], c='g', ls='', marker='.', markersize=1)
srHandleI, = srAx.plot([], [], c='r', ls='', marker='.', markersize=1)

frHandleE, = frAx.plot([], [], c='g', label='Exc', alpha=0.5)
frHandleI, = frAx.plot([], [], c='r', label='Inh', alpha=0.5)

vHandleE, = veAx.plot([], [], c='g', lw=.3)
vHandleI, = viAx.plot([], [], c='r', lw=.3)

def init():
    srHandleE.set_data([], [])
    srHandleI.set_data([], [])
    frHandleE.set_data([], [])
    frHandleI.set_data([], [])
    vHandleE.set_data([], [])
    vHandleI.set_data([], [])

    print('initalized animation')

    return srHandleE, srHandleI, frHandleE, frHandleI, vHandleE, vHandleI, 

def animate(i):
    vHandleE.set_data(voltageT[:i], voltageE[:i])
    vHandleI.set_data(voltageT[:i], voltageI[:i])

    fri = int(i / 10)
    frHandleE.set_data(FRT[:fri], FRE[:fri])
    frHandleI.set_data(FRT[:fri], FRI[:fri])

    currentTime = voltageT[i]
    sBoolE = spikesExcT <= currentTime
    sBoolI = spikesInhT <= currentTime
    srHandleE.set_data(spikesExcT[sBoolE], spikesExcI[sBoolE])
    srHandleI.set_data(spikesInhT[sBoolI], spikesInhI[sBoolI])

    print('animated frame', i)

    return srHandleE, srHandleI, frHandleE, frHandleI, vHandleE, vHandleI, 

useFPS = 30
totalFrames = int(np.round((voltageT[-1] * second) * useFPS * Hz))
useInterval = int(np.round(voltageT.size / totalFrames))
framesToSave = np.arange(0, voltageT.size, useInterval)

anim = FuncAnimation(fig1, animate, init_func=init,
                     frames=framesToSave, blit=True, repeat=False)
# anim.save('trial' + str(useTrialInd) + '.gif')

Writer = writers['ffmpeg']
writer = Writer(fps=useFPS)
anim.save('trial' + str(R.p['saveTrials'][useTrialInd] + 1) + '.mp4', writer=writer)
fig1.clear()

initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
ani

animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
an

TypeError: 'NoneType' object is not subscriptable

initalized animation
initalized animation
animated frame 0
animated frame 33
animated frame 66
animated frame 99
animated frame 132
animated frame 165
animated frame 198
animated frame 231
animated frame 264
animated frame 297
animated frame 330
animated frame 363
animated frame 396
animated frame 429
animated frame 462
animated frame 495
animated frame 528
animated frame 561
animated frame 594
animated frame 627
animated frame 660
animated frame 693
animated frame 726
animated frame 759
animated frame 792
animated frame 825
animated frame 858
animated frame 891
animated frame 924
animated frame 957
animated frame 990
animated frame 1023
animated frame 1056
animated frame 1089
animated frame 1122
animated frame 1155
animated frame 1188
animated frame 1221
animated frame 1254
animated frame 1287
animated frame 1320
animated frame 1353
animated frame 1386
animated frame 1419
animated frame 1452
animated frame 1485
